## Загрузка и обработка данных HW1

План
1. Создать git-репозиторий, где будет храниться исходный код вашего проекта.
Если вы используете приватный репозиторий – дайте преподавателям курса доступ к
нему, для возможности проверки ДЗ.
2. Добавить файл лицензии, который отражает ваш взгляд на конфиденциальность
информации, которую вы подготовите в рамках данного курса.
3. Создать код на Python, который загрузит на ваш локальный компьютер данные о
котировках ценных бумаг из списка SnP500 (apple amazon nvidia) и котировки криптовалют (BTC, ETH, SOL,
XRP).
4. Поскольку вам предстоит много работать с ними в дальнейшем, подготовьте
автоматическое отображение графиков текущей ситуации.
5. Проверьте нет ли в данных пропусков или ошибок. Проанализируйте выбросы.
Оцените, на самом ли деле это выбросы или реальные данные, с которыми предстоит
работать.

In [2]:
import ccxt
import pandas as pd
from datetime import datetime, timedelta
import yfinance as yf
from datetime import date
import plotly.express as px
import plotly.graph_objects as go
import seaborn as sns
import matplotlib.pyplot as plt
import numpy as np
from scipy import stats
from plotly.subplots import make_subplots


In [ ]:
start_date = (datetime.now() - timedelta(days=30)).strftime('%Y-%m-%d')
end_date = datetime.now().strftime('%Y-%m-%d')
# end_date = '2024-11-24' - дата на момент написания анализа


In [48]:
start_date_SnP = (datetime.now() - timedelta(days=180)).strftime('%Y-%m-%d')
end_date_SnP = datetime.now().strftime('%Y-%m-%d')

## SnP500

SnP500 загрузка данных

Я взял дневной тип данных для SnP, так как с моей точки зрения на крупных биржах логичнее торговать на HTF и по фунадменталу. Я еще я не понял как правилно оформить данные для часового графика. Ведь официалы не торгуют 24\7 из-за этого придется удалять выходыне дни и нерабочие часы на графике.   Можете подсказать как это?

In [191]:
# Тикеры для загрузки данных
tickers = ['^GSPC', 'AAPL', 'NVDA', 'AMD']

SnP_df = yf.download(['^GSPC', 'AAPL', 'NVDA', 'AMD'], start=start_date_SnP, end=end_date_SnP, interval='1d').reset_index().drop(columns=['Adj Close'])


[*********************100%***********************]  4 of 4 completed
C:\Users\Admin\AppData\Local\Temp\ipykernel_13856\2701513021.py:4: PerformanceWarning:

dropping on a non-lexsorted multi-index without a level parameter may impact performance.



In [192]:
SnP_df.columns
indexes =['Date','Close','High','Low','Open','Volume']

In [193]:
SnP_dс = {}
for ticker in tickers:
    data_list = []
    for index in indexes:
        if (index, ticker) in SnP_df.columns:
            data = SnP_df.loc[:, (index, ticker)]
            data.name = f'{index}'  
            data_list.append(data)
    if data_list:
        SnP_dс[f'{ticker}_df'] = pd.concat(data_list, axis=1)

# Обновляем каждый DataFrame в словаре и добавляем столбец с изменениями цены
for df_name, df in SnP_dс.items():
    
    # Находим колонку с ценами закрытия
        close_column = [col for col in df.columns if 'Close' in col]
    
        if close_column:
            close_column = close_column[0]  # Берём первую найденную колонку с "Close"
            # Добавляем столбец с изменениями цены
            df['Chg'] = df[close_column].diff()
        else:
            print(f"Колонка с закрытием для тикера {ticker} не найдена.")
        
        # Обновляем DataFrame в словаре
        SnP_dс[df_name] = df.drop(0)
# Объединяем все датафреймы в один

# Объединяем все датафреймы в один и убираем '_df' из названий столбцов
combined_df = pd.concat([df.add_prefix(f'{ticker}_') for ticker, df in SnP_dс.items()], axis=1)
combined_df.insert(0, 'Date', SnP_df['Date'])
combined_df.columns = [col.replace('_df', '') for col in combined_df.columns]

SnP_df = combined_df


SnP график

In [194]:
SnP_df

Date  ^GSPC_Close   ^GSPC_High    ^GSPC_Low   ^GSPC_Open  \
1   2024-05-29  5266.950195  5282.270020  5262.700195  5278.729980   
2   2024-05-30  5235.479980  5260.209961  5222.100098  5259.770020   
3   2024-05-31  5277.509766  5280.330078  5191.680176  5243.209961   
4   2024-06-03  5283.399902  5302.109863  5234.319824  5297.149902   
5   2024-06-04  5291.339844  5298.799805  5257.629883  5278.240234   
..         ...          ...          ...          ...          ...   
121 2024-11-18  5893.620117  5908.120117  5865.950195  5874.169922   
122 2024-11-19  5916.979980  5923.509766  5855.290039  5870.049805   
123 2024-11-20  5917.109863  5920.669922  5860.560059  5914.339844   
124 2024-11-21  5948.709961  5963.319824  5887.259766  5940.580078   
125 2024-11-22  5969.339844  5972.899902  5944.359863  5944.359863   

     ^GSPC_Volume  ^GSPC_Chg  AAPL_Close   AAPL_High    AAPL_Low  ...  \
1      3552750000 -39.089844  190.289993  192.250000  189.509995  ...   
2      3818750000 -31.470215  191.289993  192.179993  190.630005  ...   
3      5437160000  42.029785  192.250000  192.570007  189.910004  ...   
4      4046920000   5.890137  194.029999  194.990005  192.520004  ...   
5      3707900000   7.939941  194.350006  195.320007  193.029999  ...   
..            ...        ...         ...         ...         ...  ...   
121    3983860000  23.000000  228.020004  229.740005  225.169998  ...   
122    4036940000  23.359863  228.279999  230.160004  226.660004  ...   
123    3772620000   0.129883  229.000000  229.929993  225.889999  ...   
124    4230120000  31.600098  228.520004  230.160004  225.710007  ...   
125    4141420000  20.629883  229.869995  230.720001  228.059998  ...   

       NVDA_Low   NVDA_Open  NVDA_Volume  NVDA_Chg   AMD_Close    AMD_High  \
1    110.901001  113.050003    557442000  0.923996  165.139999  168.479996   
2    109.663002  114.650002    487350000 -4.324997  166.750000  168.750000   
3    106.940002  112.519997    613263000 -0.866997  166.899994  169.500000   
4    112.002998  113.621002    438392000  5.366997  163.550003  171.080002   
5    114.044998  115.716003    403324000  1.436996  159.990005  164.830002   
..          ...         ...          ...       ...         ...         ...   
121  137.149994  139.500000    221866000 -1.830002  138.929993  140.899994   
122  140.990005  141.320007    227834900  6.860001  139.389999  139.750000   
123  142.729996  147.410004    309871700 -1.119995  137.600006  140.770004   
124  140.699997  149.350006    400946600  0.779999  137.490005  140.279999   
125  141.100006  145.929993    235772200 -4.720001  138.350006  139.130005   

        AMD_Low    AMD_Open  AMD_Volume   AMD_Chg  
1    162.910004  167.460007    56537500 -6.470001  
2    163.800003  167.899994    46479900  1.610001  
3    160.070007  166.649994    64331900  0.149994  
4    160.910004  170.820007    59157600 -3.349991  
5    158.869995  162.839996    48157200 -3.559998  
..          ...         ...         ...       ...  
121  137.210007  138.190002    38782400  4.029999  
122  137.139999  137.410004    23131400  0.460007  
123  135.479996  138.960007    28843100 -1.789993  
124  134.929993  138.869995    29311400 -0.110001  
125  137.039993  137.350006    21742700  0.860001  

[125 rows x 25 columns]

In [195]:
for ticker in tickers:
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=SnP_df['Date'], y=SnP_df[f'{ticker}_Close'], mode='lines', name=f'{ticker} Close Price'))
    fig.update_layout(
        title=f'Цены {ticker} за последние пол года',
        xaxis_title='Дата',
        yaxis_title='Цена (USD)',
        xaxis_rangeslider_visible=True
    )
    fig.show()

Анализ данных SNP

In [196]:
for ticker in tickers:
    SnP_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 125 entries, 1 to 125
Data columns (total 25 columns):
 #   Column        Non-Null Count  Dtype         
---  ------        --------------  -----         
 0   Date          125 non-null    datetime64[ns]
 1   ^GSPC_Close   125 non-null    float64       
 2   ^GSPC_High    125 non-null    float64       
 3   ^GSPC_Low     125 non-null    float64       
 4   ^GSPC_Open    125 non-null    float64       
 5   ^GSPC_Volume  125 non-null    int64         
 6   ^GSPC_Chg     125 non-null    float64       
 7   AAPL_Close    125 non-null    float64       
 8   AAPL_High     125 non-null    float64       
 9   AAPL_Low      125 non-null    float64       
 10  AAPL_Open     125 non-null    float64       
 11  AAPL_Volume   125 non-null    int64         
 12  AAPL_Chg      125 non-null    float64       
 13  NVDA_Close    125 non-null    float64       
 14  NVDA_High     125 non-null    float64       
 15  NVDA_Low      125 non-null    float64   

За последние 180 дней было 126 дней торгов нулевых значений нет -1 для расчета параметра change 


Анализ выбросов и распределения SnP

In [202]:
fig = make_subplots(
    rows=3, cols=1,
    subplot_titles=tickers)

ind = 0
for i in range(1, 4):
    column = tickers[ind]
    if column + '_Chg' in SnP_df.columns:
        fig.add_trace(go.Scatter(x=SnP_df.index, y=SnP_df[column + '_Chg'], name=column), row=i, col=1)
    else:
        print(f"Warning: Column {column + '_Chg'} not found in DataFrame.")
    ind += 1

fig.show()

In [205]:
for ticker in tickers:
    fig = px.histogram(SnP_df, x=f'{ticker}'+'_Chg',
        marginal="violin",
        )
    fig.show()

## Крипто 

Крипто загрузка данных

In [198]:
bybit   = ccxt.bybit()
print(bybit.id, bybit.load_markets())

bybit {'BTC/USDT': {'id': 'BTCUSDT', 'lowercaseId': None, 'symbol': 'BTC/USDT', 'base': 'BTC', 'quote': 'USDT', 'settle': None, 'baseId': 'BTC', 'quoteId': 'USDT', 'settleId': None, 'type': 'spot', 'spot': True, 'margin': True, 'swap': False, 'future': False, 'option': False, 'index': False, 'active': True, 'contract': False, 'linear': None, 'inverse': None, 'subType': None, 'taker': 0.001, 'maker': 0.001, 'contractSize': None, 'expiry': None, 'expiryDatetime': None, 'strike': None, 'optionType': None, 'precision': {'amount': 1e-06, 'price': 0.01, 'cost': None, 'base': None, 'quote': None}, 'limits': {'leverage': {'min': 1.0, 'max': None}, 'amount': {'min': 4.8e-05, 'max': 71.73956243}, 'price': {'min': None, 'max': None}, 'cost': {'min': 1.0, 'max': 4000000.0}}, 'marginModes': {'cross': None, 'isolated': None}, 'created': None, 'info': {'symbol': 'BTCUSDT', 'baseCoin': 'BTC', 'quoteCoin': 'USDT', 'innovation': '0', 'status': 'Trading', 'marginTrading': 'utaOnly', 'stTag': '0', 'lotSiz

In [199]:

exchange = ccxt.bybit({
    'rateLimit': 1000,
    'enableRateLimit': True,
})

# Настройки
pairs = ['BTC/USDT', 'ETH/USDT', 'SOL/USDT', 'XRP/USDT']  
timeframe = '1h' 
since = int((datetime.now() - timedelta(days=30)).timestamp() * 1000) 
limit = 1000  

def fetch_historical_data(token, timeframe, since):
    all_data = []
    all_data.extend(exchange.fetch_ohlcv(token, timeframe, since, limit=limit))
    df = pd.DataFrame(all_data, columns=['timestamp', 'open', 'high', 'low', 'close', 'volume'])
    df['timestamp'] = pd.to_datetime(df['timestamp'], unit='ms')
    df = df.rename(columns={col: f"{token.split('/')[0]}_{col}" for col in df.columns if col != 'timestamp'})
    return df

crypto_dc = {token: fetch_historical_data(token, timeframe, since) for token in pairs}

btc_df = crypto_dc['BTC/USDT']
eth_df = crypto_dc['ETH/USDT']
sol_df = crypto_dc['SOL/USDT']
xrp_df = crypto_dc['XRP/USDT']


KeyboardInterrupt: 

In [ ]:
crypto_df = crypto_dc[pairs[0]].set_index('timestamp')

for token in pairs[1:]:
    crypto_df = crypto_df.join(crypto_dc[token].set_index('timestamp'), how='left', rsuffix=f'_{token.split("/")[0]}')

crypto_df.reset_index(inplace=True)
tokens = ['BTC', 'ETH', 'SOL', 'XRP']
for token in tokens:
    if token + '_close' in crypto_df.columns:
        crypto_df[token + '_chg'] = crypto_df[token + '_close'].diff()
crypto_df.drop(0,inplace=True)


Крипто график

In [9]:
for token, df in crypto_dc.items():
    asset = token.split('/')[0]
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=df['timestamp'], y=df[f'{asset}_close'], mode='lines', name=f'{asset} Price'))
    fig.update_layout(
        title=f'Цены {asset} за последний месяц',
        xaxis_title='Дата',
        yaxis_title='Цена (USDT)',
        xaxis_rangeslider_visible=True
    )
    fig.show()


Анализ данных крипта

In [13]:
for token in pairs:
    crypto_dc[f'{token}'].info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 720 entries, 0 to 719
Data columns (total 6 columns):
 #   Column      Non-Null Count  Dtype         
---  ------      --------------  -----         
 0   timestamp   720 non-null    datetime64[ns]
 1   BTC_open    720 non-null    float64       
 2   BTC_high    720 non-null    float64       
 3   BTC_low     720 non-null    float64       
 4   BTC_close   720 non-null    float64       
 5   BTC_volume  720 non-null    float64       
dtypes: datetime64[ns](1), float64(5)
memory usage: 33.9 KB
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 720 entries, 0 to 719
Data columns (total 6 columns):
 #   Column      Non-Null Count  Dtype         
---  ------      --------------  -----         
 0   timestamp   720 non-null    datetime64[ns]
 1   ETH_open    720 non-null    float64       
 2   ETH_high    720 non-null    float64       
 3   ETH_low     720 non-null    float64       
 4   ETH_close   720 non-null    float64       
 5   ETH_vol

из 720 значений, 0 являются Null, данные не поврежденны

График дифиренцированных данных

In [14]:
fig = make_subplots(
    rows=3, cols=1,
    subplot_titles=tokens)

ind = 0
for i in range(1, 4):
    column = tokens[ind]
    if column + '_chg' in crypto_df.columns:
        fig.add_trace(go.Scatter(x=crypto_df.index, y=crypto_df[column + '_chg'], name=column), row=i, col=1)
    else:
        print(f"Warning: Column {column + '_chg'} not found in DataFrame.")
    ind += 1

fig.show()


График выбросов и распределения

In [ ]:
for token in tokens:
    fig = px.histogram(crypto_df, x=f'{token}'+'_chg',
        marginal="violin",
        )
    fig.show()

Анализ выбросов Крипто

Выводы пишу на 24.11
- контекст последнего месяца 
- позитив альтов и битка 
- У всех активов наблюдается отклонение медианы в положительную сторону что обусловленно позитивом рынком
- Во всех данных, кроме XRP, присутствуют небольшие выбросы. Малая часть из них связана со свечами дампа/пампа. С моей точки зрения, данные стоит оставить, так как бот должен выявлять ситуации, ведущие к таким аномальным движениям. Однако, если бот создается для торговли в узком диапазоне, такие выбросы можно удалить.
- XRP это одельный случай, это монета из топ-100, это ознчает что 90% времени монета надится в малом торговом диопозоне и любые сильные движения становятся выбросами, поэтому их тоже не стоит удалять


Итог 
1. Создать git-репозиторий - Сделал

2. Добавить файл лицензии, который отражает ваш взгляд на конфиденциальность
информации, которую вы подготовите в рамках данного курса. 

(не понял, тут вопрос сделать шифрование данных как мы делали на одной из лекций или что-то другое?) 

3. Создать код на Python, который загрузит на ваш локальный компьютер данные о
котировках ценных бумаг из списка SnP500(apple amazon nvidia) и котировки криптовалют (BTC, ETH, SOL,
XRP). 

(подключился к yfinance и bybit api через ccxt)

4. Поскольку вам предстоит много работать с ними в дальнейшем, подготовьте
автоматическое отображение графиков текущей ситуации. 

(Нужно ли мне написать код для реалтайм обновления данных, или тут имеется в виду подклчене через API)

(Пока-что сделал так что при каждой компиляуии берутся данные за прошедший месяц)

5. Проверьте нет ли в данных пропусков или ошибок. Проанализируйте выбросы.
Оцените, на самом ли деле это выбросы или реальные данные, с которыми предстоит
работать.